# 1. Approximating sin(x)

In [1]:
using LinearAlgebra

In [2]:
# number of expansion coefficients
pmax = 10

10

In [3]:
# number of evalulation points
npoints = 1001
x = LinRange(0, π/2, npoints)

1001-element LinRange{Float64, Int64}:
 0.0,0.0015708,0.00314159,0.00471239,…,1.56608,1.56765,1.56923,1.5708

In [4]:
# Target function
fstar(x) = sin(x)

fstar (generic function with 1 method)

In [5]:
# Matrix, 'A', which encodes the x's to each power evaluated at each of our p points and at each point in linrange
# the i'th row is x(i)^p with each column being p in 0 to 10
# each row is a different point in the linrange (1000 of them)
# this matrix is going to be multiplied by the coefficients vector which has p entries
A = [x[i]^p for i in 1:npoints, p in 0:pmax]

1001×11 Matrix{Float64}:
 1.0  0.0         0.0          0.0         …   0.0           0.0
 1.0  0.0015708   2.4674e-6    3.87578e-9      5.82209e-26   9.14532e-29
 1.0  0.00314159  9.8696e-6    3.10063e-8      2.98091e-23   9.3648e-26
 1.0  0.00471239  2.22066e-5   1.04646e-7      1.14596e-21   5.40022e-24
 1.0  0.00628319  3.94784e-5   2.4805e-7       1.52623e-20   9.58956e-23
 1.0  0.00785398  6.1685e-5    4.84473e-7  …   1.13713e-19   8.93097e-22
 1.0  0.00942478  8.88264e-5   8.37169e-7      5.86733e-19   5.52982e-21
 1.0  0.0109956   0.000120903  1.32939e-6      2.34942e-18   2.58333e-20
 1.0  0.0125664   0.000157914  1.9844e-6       7.81428e-18   9.81971e-20
 1.0  0.0141372   0.000199859  2.82545e-6      2.2556e-17    3.18877e-19
 1.0  0.015708    0.00024674   3.87578e-6  …   5.82209e-17   9.14532e-19
 1.0  0.0172788   0.000298556  5.15867e-6      1.37282e-16   2.37206e-18
 1.0  0.0188496   0.000355306  6.69736e-6      3.00407e-16   5.66254e-18
 ⋮                                 

In [6]:
# now we want to make our vector of sin(x) values evaluated at each x(i) point to compare (find difference)
# with the polynomial approximation
b = fstar.(x)

1001-element Vector{Float64}:
 0.0
 0.001570795680830879
 0.0031415874858795635
 0.004712371539373423
 0.006283143965558951
 0.007853900888711334
 0.009424638433144006
 0.010995352723218221
 0.012566039883352607
 0.014136696038032732
 0.015707317311820675
 0.017277899829364566
 0.018848439715408175
 ⋮
 0.9998507259473718
 0.9998766324816606
 0.9999000719197535
 0.9999210442038161
 0.9999395492821014
 0.9999555871089498
 0.9999691576447897
 0.9999802608561371
 0.999988896715596
 0.9999950652018582
 0.9999987662997035
 1.0

In [7]:
# after taking taking the gradient of (|b>-A|c>)^2 and setting it to zero (least squares method),
# we solve the equation and obtain (A^T)A|c> = (A^T)|b> therefore we can find
# the vector c by defining c = (A'*A) \ (A' * b). Here the \ backslash means that the A' * b is in the 
# numerator and this makes things better with the matrix dimensions than using the / forward slash 
c = (A'*A) \ (A' * b)

11-element Vector{Float64}:
 -1.5432412938738428e-9
  1.0000001101406408
 -1.8963286181622485e-6
 -0.16665274164716812
 -5.415555203824245e-5
  0.008457137025125839
 -0.0001748160797612103
 -4.4073151077789855e-5
 -8.3041153964433e-5
  2.7740737910503198e-5
 -3.278005301152776e-6

In [8]:
# polynomial function that approximates fstar:
f(c, x) = sum(c[p+1] * x^p for p in 0:pmax)

f (generic function with 1 method)

In [9]:
using WGLMakie

In [10]:
fig = Figure()
Axis(fig[1,1])
xx = LinRange(0, π/2, 1001)
yy = [f(c,x) for x in xx]
lines!(xx, fstar.(xx),color=:hotpink,linewidth=4)
lines!(xx, yy,color=:turquoise2,linewidth=4)
fig
# Note there are two lines here. They just match super well!!

In [11]:
# Here I'm going to plot it again for a larger range just to show that the approximate function 
# is pretty terrible for a larger domain:
fig = Figure()
Axis(fig[1,1])
xx = LinRange(0, 7π/4, 1001)
yy = [f(c,x) for x in xx]
lines!(xx, fstar.(xx),color=:hotpink,linewidth=4)
lines!(xx, yy,color=:turquoise2,linewidth=4)
fig
# you can see the approximation is pretty good until π and then it diverges away from sin(x). 
# note this would probably get a lot better if we kept more terms in the polynomial

# 2. L2 norm error

In [12]:
function L2error(vector1, vector2)
    diffvect = vector1 .- vector2
    return sqrt((1/length(vector1))*sum(diffvect.^2))
end

L2error (generic function with 1 method)

In [13]:
#Checking that it works:
a =[1, 2, 3]
d = [4, 5, 6]
L2error(a,d)
# should be equal to 3

3.0

In [14]:
vecf = [f(c,i) for i in x];
vecsin = [sin(i) for i in x];

In [15]:
# now we want to find the L2 norm for the distance between vector b (all the values of sin(x[i])) and 
# vector f(c, x) (approximation polynomial evaluated at each x[i])
L2error(vecsin,vecf) 

3.372451495510846e-10

In [16]:
# now let's try this for a different pmax. 
# I'll define a general function that approximates general functions

function sin_approx(pmax, npoints, lower_bound, upper_bound)
    
    x = LinRange(lower_bound, upper_bound, npoints)

    A = [x[i]^p for i in 1:npoints, p in 0:pmax]
    b = sin.(x)
    c = (A'*A) \ (A' * b)

    return sum(c[p+1] * x.^p for p in 0:pmax)
end

sin_approx (generic function with 1 method)

In [17]:
# now let's try it for pmax = 12 to see if the error decreases

newvecf = sin_approx(100, 1001, 0, π/2)


L2error(vecsin,newvecf)
# this just got worse??
# it keeps getting worse with more terms!!!

2.705945518418829e-7

In [18]:
# let's plot the error for different pmax values to see how the error changes (maybe it's a floating point error)
errorvec = zeros(95)
p = LinRange(6,100,95)
for i in 1:95
    newvecf = sin_approx(i+5, 1001, 0, π/2)
    errorvec[i] = L2error(vecsin, newvecf)
end 

fig = Figure()
Axis(fig[1,1])
plot!(p, errorvec,color=:turquoise2)
fig
# I cut out the first five points (that represented the error when keeping just 1, 2, 3, 4, or 5 terms) becase
# their error was very large and they forced the other error points to mainly be confined to a line close to 
# zero. So we see that yes the error gets smaller after the first five or so points, but later on it gets
# a bit stochastic and potentially floating point error gives us issues down the line.
# It doesn't seem to get quite as low as 1.0e-10, so let me plot again just around a few points and check

In [19]:
# Making a base 10 log plot so we can see the order of magnitude more clearly
errorvec = zeros(30)
p = LinRange(1,30,30)
for i in 1:30
    newvecf = sin_approx(i, 1001, 0, π/2)
    errorvec[i] = L2error(vecsin, newvecf)
end 

fig = Figure()
Axis(fig[1,1])
lines!(p, log.(10,errorvec); color=:hotpink,linewidth=4)
fig
# Now we see that the error is seemingly the lowest at pmax = 9

In [20]:
newvecf = sin_approx(9, 1001, 0, π/2)
errorvec = L2error(vecsin, newvecf)
# Yes! We did indeed get down to e-11

2.4109793202771267e-11

In [21]:
# It doesn't seem like we can get any lower than this sadly, and therefore it seems like
# we can't get to 1.0e-20. I think the reason probably has to do with floating point error.

# 3. Modifying for sin's antisymmetry

In [22]:
# Editing prior code to make it every other p value, but only the odds (2p+1)
# note that 'as' stands for anti symmetric
# also note that pmax isn't the same pmax anymore, but is rather the pmax in 2p+1
# this means that sin_approx and sin_approx_as will have the same number of polynomials because they both
# index by p

function sin_approx_as(pmax, npoints, lower_bound, upper_bound)
    
    x = LinRange(lower_bound, upper_bound, npoints)

    A_as = [x[i]^(2p+1) for i in 1:npoints, p in 0:pmax]
    b = sin.(x)
    c_as = (A_as'*A_as) \ (A_as' * b)

    return sum(c_as[p+1] * x.^(2p+1) for p in 0:pmax)
end

sin_approx_as (generic function with 1 method)

In [23]:
newvecf_as = sin_approx_as(30, 1001, 0, π/2)

L2error(vecsin,newvecf_as)

2.6527707990170927e-9

In [24]:
#let's do a base 10 log plot 
errorvec = zeros(30)
p = LinRange(1,30,30)
for i in 1:30
    newvecf = sin_approx_as(i, 1001, 0, π/2)
    errorvec[i] = L2error(vecsin, newvecf)
end 

fig = Figure()
Axis(fig[1,1])
lines!(p, log.(10,errorvec);color=:turquoise2,linewidth=4)
fig

In [25]:
newvecf_as_min = sin_approx_as(6, 1001, 0, π/2)
errorvec_as_min = L2error(vecsin, newvecf_as_min)
# oooo nice we get into the e-12 range

1.5834090365300181e-12

In [26]:
# now let's compare the result for the same number of polynomials:
# I'll plot both just so we're not biased as to which points to pick, and I'll do a log
# plot to show the order of magnitudes more clearly
errorvec = zeros(50)
errorvec_as = zeros(50)
p = LinRange(1,50,50)
for i in 1:50
    newvecf = sin_approx(i, 1001, 0, π/2)
    newvecf_as = sin_approx_as(i, 1001, 0, π/2)
    errorvec[i] = L2error(vecsin, newvecf)
    errorvec_as[i] = L2error(vecsin, newvecf_as)
end 

fig = Figure()
Axis(fig[1,1])
lines!(p, log.(10,errorvec); color=:cyan, linewidth=4)
lines!(p, log.(10,errorvec_as); color=:hotpink, linewidth=4)
fig

In [27]:
# Interesting! So we can see that the anti-symmetric does better for the first 8 or so terms and then the
# errors seem to even out past about 13 terms.

# 4.a. Analytic Derivative of Approximate Function

Derivative of f(c, x) = ∑ₚcₚxᵖ is simply ∑ₚcₚpxᵖ⁻¹   
Defining a new function to approximate the derivative:   
g(d, x) = ∑ₚdₚxᵖ, we want to re-express the d coefficients in terms of the c coefficients

Note that if we have f(x) = c₀+c₁x+c₂x²+c₃x³ (we'll cut this off for ease with matrices now, but one could
make this an infinite sum)   
then f'(x) = c₁+2c₂x+3c₃x²   
meaning that the d coefficients here would be   
d₀ = c₁, d₁ = 2c₂, d₃ = 3c₃.
We can represent this in a matrix:

In [28]:
A = [0 1 0 0; 0 0 2 0; 0 0 0 3]

3×4 Matrix{Int64}:
 0  1  0  0
 0  0  2  0
 0  0  0  3

If we take this matrix A and multiply it with vector c which stores the four c coefficients, we get exactly the three d coefficients! Note we can extend this matrix for an arbitrary amount of coefficients. If these are kept finite, also note that we must make the matrix have one fewer rows than columns. This is because we will end up with one fewer coefficients after differentiating because the first coefficient with no factor of x will dissapear. 

# 4.b. Numerical Derivative of Approximate Function

In [29]:
using SparseArrays

In [47]:
# Creating general D:
function deriv_linear_transf(size_vec)
    
    row = collect(1:size_vec-1)
    col = collect(2:size_vec)
    entries = collect(1:size_vec-1)
    D = sparse(row,col,entries)
    return D

end

deriv_linear_transf (generic function with 1 method)

In [49]:
deriv_linear_transf(10)
# Testing it out

9×10 SparseMatrixCSC{Int64, Int64} with 9 stored entries:
 ⋅  1  ⋅  ⋅  ⋅  ⋅  ⋅  ⋅  ⋅  ⋅
 ⋅  ⋅  2  ⋅  ⋅  ⋅  ⋅  ⋅  ⋅  ⋅
 ⋅  ⋅  ⋅  3  ⋅  ⋅  ⋅  ⋅  ⋅  ⋅
 ⋅  ⋅  ⋅  ⋅  4  ⋅  ⋅  ⋅  ⋅  ⋅
 ⋅  ⋅  ⋅  ⋅  ⋅  5  ⋅  ⋅  ⋅  ⋅
 ⋅  ⋅  ⋅  ⋅  ⋅  ⋅  6  ⋅  ⋅  ⋅
 ⋅  ⋅  ⋅  ⋅  ⋅  ⋅  ⋅  7  ⋅  ⋅
 ⋅  ⋅  ⋅  ⋅  ⋅  ⋅  ⋅  ⋅  8  ⋅
 ⋅  ⋅  ⋅  ⋅  ⋅  ⋅  ⋅  ⋅  ⋅  9

In [74]:
function sin_approx_coeff(pmax, npoints, lower_bound, upper_bound)
    
    x = LinRange(lower_bound, upper_bound, npoints)

    A = [x[i]^p for i in 1:npoints, p in 0:pmax]
    b = sin.(x)
    c = (A'*A) \ (A' * b)

    return c
end

sin_approx_coeff (generic function with 1 method)

In [75]:
function sin_deriv_lin_transf(pmax, npoints, lower_bound, upper_bound)
    
    approx_sin_coeff = sin_approx_coeff(pmax, npoints, lower_bound, upper_bound)
    
    d = deriv_linear_transf(pmax+1)*approx_sin_coeff
    
    g = sum(d[p+1] * x.^p for p in 0:pmax-1)

    return g
end

sin_deriv_lin_transf (generic function with 1 method)

In [77]:
sin_deriv_lin_transf(9,1001,0,π/2)

#plotting to check
fig = Figure()
Axis(fig[1,1])
xx = LinRange(0, π/2, 1000)
yy = [g[i] for i in 1:1000]
lines!(xx, yy, color=:turquoise2,linewidth=4)
fig
# Yay it looks like a cosine!!

In [81]:
function cos_approx(pmax, npoints, lower_bound, upper_bound)
    
    x = LinRange(lower_bound, upper_bound, npoints)

    A = [x[i]^p for i in 1:npoints, p in 0:pmax]
    b = cos.(x)
    c = (A'*A) \ (A' * b)

    return sum(c[p+1] * x.^p for p in 0:pmax)
end

cos_approx (generic function with 1 method)

In [87]:
# Now to look at the error
errorvec = zeros(25)
p = LinRange(1,25,25)
for i in 1:25
    sinderiv = sin_deriv_lin_transf(i, 1001, 0, π/2)
    veccos = cos_approx(i, 1001, 0, π/2)
    errorvec[i] = L2error(veccos, sinderiv)
end 

fig = Figure()
Axis(fig[1,1])
lines!(p,log.(10,errorvec); color=:turquoise2,linewidth=4)
fig
# Looks pretty good!